
# Künstlicher Assistent für die Annotation des Märchens

## Google Colab Arbeitplatz vorbereiten

## Aggregation des Korpus von Trainingsdaten 

[Zelle # 1]

1-3: Die Variable 'tupNum', 'repert' und 'ausnahme' gelten für die Auswahl der in dem Trainingsdatenrepositorium angelegte Texte mit dem gesuchten Typ und dem Herkunftsrepertoire. Sowohl die Variable 'typNum' ails auch 'repert' kann mit leeren Anführungszeichen dargestellt werden, für die Variable 'ausnahme' ist entweder ein unwahrscheinlicher Wert (z.B. 'xxyyzz') oder der Wert womit man eine bestimmte Gruppe  von Daten aus der Wahl ausschließen kann eine Pflicht.

4-8: Jedes Mal bei der Aggregation des Korpus von Trainingsdaten wird der gleichnamige alte Korpus gelöscht.


In [119]:
def entfernen(var):
    import os
    if os.path.exists(var):
        os.remove(var)
entfernen('episode_binar_roh.csv')

[Zelle # 2]

1-59: Aggregation der Datei 'episode_temp_train.csv' (eine Funktion). Die im Ordner „Trainingsdaten“ angelegte TXT Dateien werden in der CSV Datei aggregiert und in das root Repositorium verlegt.

60-66: Umwandlung 'episode_temp_train.csv' in die Datei 'episode_string_train.csv'.

67-72: 'episode_string_train.csv' laden, von den überflüssigen Zeichen bereinigen und ins Trainingsdatenkorpus 'episode_binar_train.csv' umwandeln.

ab-73: Unnotige Aggregationen werden gelöscht.

In [120]:
def clean(line):
    line = line.replace("\n"," ").strip()
    line = line.replace("ä","ae").replace("ü","ue").replace("ö","oe")
    line = line.replace("ß","ss").replace(",","").replace("«","")
    line = line.replace("»","").replace(".","").replace(":","")
    line = line.replace(";","").replace('"',"")
    line = line.replace("?","").replace("!","").replace("á","a")
    line = line.replace(",","").replace("\t"," ").replace("'","")
    line = line.replace("‹","").replace("›","").replace("-"," ")
    line = line.replace("'('","").replace("')'","").replace('>','')
    line = line.replace("    "," ").replace("   "," ").replace("  "," ")
    line = line.replace('–','').replace('—','').replace('<','')
    line = line.replace("Â", "A").replace("ø", "oe").replace('“','')
    line = line.replace('„','').replace('(','').replace(')','')
    line = line.replace("‚", "").replace(']','').replace('[','')
    if line == "": 
        return
    line=line.split("|")
    line[0]=line[0].split("|")[0]
    for i, _ in enumerate(line):
        if (i !=0) and (i!=2):
            line[i]=line[i].lower()
    flex=[]
    try:
        flex=line[1].split("")
    except:
        pass
    value=str(line)
    line=str(line)   
    flex.append(line)
    ret=[]
    for i in flex:
        ret.append((i,value[0]))
    return ret
def write_back(words, temp):
    with open(temp, "a", encoding='utf-8') as output:      
        for word in words:
            as_lex = word[0]
            full_word = '"' + as_lex + '"'
            for sub_word in word[1:]:
                full_word += " , "  '"' + sub_word + '"'
            full_word +="\n"
            output.write(full_word)
def aggreg(temp, ordner):
    import glob
    with open(temp, "w", encoding='utf-8') as output:
        output.write ("quelle,episode,index_string,index_binar\n")
    sorted_files=sorted(glob.glob(ordner))
    pairs = []
    for file in sorted_files:
        with open(file, 'r', encoding='utf-8', errors='ignore') as episode:
            for line in episode.readlines():
                clean_words = clean(line)
                pairs = pairs + clean_words
    write_back(pairs, temp)
temp = "episode_temp_roh.csv"
ordner = "Datendepot/*.txt"
aggreg(temp, ordner)
fin = open('episode_temp_roh.csv','r', encoding ='utf-8')
fout = open('episode_string_roh.csv', "wt", encoding ='utf-8')
for kfz in fin:
    fout.write(kfz.replace(', "["',"").replace('"[', "").replace(']"',"")
               .replace("', '", "','").replace(" '", "'"))
fin.close()
fout.close()

fin = open('episode_string_roh.csv','r', encoding='utf-8') 
fout = open('episode_binar_roh.csv', "wt", encoding='utf-8')
for efz in fin:
    fout.write(efz.replace("'","").replace(',,0,0',',test,0,0'))             
fin.close()
fout.close()
entfernen('episode_temp_roh.csv')
entfernen('episode_string_roh.csv')

##  Herstellung des Modells und der prototypischen Metaepisode 

[Zelle # 3]

1-5: Trainingdatenkorpus zugreiffen und der im Datenfeld 'index_string' eingetragene Merkmalen mitsamt der Vorkommenshäufigkeitsrate einbelden.

In [121]:
import pandas as pd
from collections import Counter
df = pd.read_csv('episode_binar_roh.csv',  encoding='utf-8')
indexliste=Counter(df.index_string)
print(indexliste, sep='\n')

Counter({'0': 8823, 'xxx': 1})


[Zelle # 4]

1: In den obeneingeblendete Merkmalen eine Episode Kopieren und hier als Wert der Variable 'gesep' einfügen. 

In [122]:
gesep = 'xxx'

[Zelle # 5]

1-6: In Trainingsdaten die gesuchte Episode ('gesep') mit Einsen (1), den Rest mit Nullen (0) etikettieren und die Änderung speichern.

In [123]:
for i, gesuchte_episode in enumerate(df.index_string):
    if (gesuchte_episode == gesep):
        df.index_binar[i]='1'
    else: 
            df.index_binar[i]='0'
df.to_csv('episode_binar_train.csv', encoding='utf-8', index=False)

C:\Users\elguj\AppData\Local\Temp/ipykernel_18340/1130496417.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.index_binar[i]='1'
C:\Users\elguj\AppData\Local\Temp/ipykernel_18340/1130496417.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.index_binar[i]='0'


[Zelle # 6]

1-4: Im Trainingsdatenkorpus die Datenfelder für Probetexte (X_train) und für die Merkmalen (y_train) bestimmen und die Bilanz zwischen negativ (0) und positiv (1) etikettierten Datensätzen betrachten ( s. Counter).

In [124]:
X_train=(df['episode'])
y_train=(df['index_binar'])
indexliste=Counter(df.index_binar)
print(indexliste, sep='\n')

Counter({0: 8823, 1: 1})


[Zelle # 7]

1: Die in die eckige Klammern eingetragene Wörter werden zusätzlich in die vorhandene Stopwörter-Liste eingefügt. Einzelnes Wort muss dabei mit Anführungszeichen umgeschlossen und von andren Wörter durch das Komma getrennt werden, ein Beispiel: ['mein','dein']. 

2-6: Datenfeld 'episode' von konwentionelen und von uns eingegebenen Stoppwörter bereinigen. 

In [125]:
custom_stop_word_list=[]
import nltk
nltk.download('stopwords')
from nltk.corpus import stopwords
NLTK_stop_words_list=stopwords.words('german')
de = custom_stop_word_list + NLTK_stop_words_list

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\elguj\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


[Zelle # 8]

1-8: Einrichtung einer sciki-learn Pipeline mit Klassen LogisticRegression, TfidVectorizer und GridSearchCV. 

9-10: Modell auswerten (s. Bester Score aus der Kreuzvalidierung:).

In [126]:
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import GridSearchCV
from sklearn.pipeline import make_pipeline
pipe = make_pipeline(TfidfVectorizer(min_df=3, stop_words=de, ngram_range=(1,1), norm=None), 
                     LogisticRegression())
param_grid = {'logisticregression__C': [0.001, 0.01, 0.1, 1, 10]}     
grid = GridSearchCV(pipe, param_grid, cv=5)
grid.fit(X_train, y_train)
print("Bester Score aus der Kreuzvalidierung: {:.2f}".format(grid.best_score_))

C:\Users\elguj\anaconda3\lib\site-packages\sklearn\model_selection\_split.py:684: UserWarning: The least populated class in y has only 1 members, which is less than n_splits=5.
  warnings.warn(
C:\Users\elguj\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py:378: FitFailedWarning: 
5 fits failed out of a total of 25.
The score on these train-test partitions for these parameters will be set to nan.
If these failures are not expected, you can try to debug them by setting error_score='raise'.

Below are more details about the failures:
--------------------------------------------------------------------------------
5 fits failed with the following error:
Traceback (most recent call last):
  File "C:\Users\elguj\anaconda3\lib\site-packages\sklearn\model_selection\_validation.py", line 686, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "C:\Users\elguj\anaconda3\lib\site-packages\sklearn\pipeline.py", line 382, in fit
    self._final_estimator.fi

Bester Score aus der Kreuzvalidierung: nan


[Zelle # 9]

1-6: Aus dem Modell die Liste der positiven und negativen Merkmalen extrachieren, Zahl der Merkmalen einblenden (s. Gesamte Anzahl der Wörter:).

In [127]:
import numpy as np
vectorizer = grid.best_estimator_.named_steps["tfidfvectorizer"]
max_value = vectorizer.transform(X_train).max(axis=0).toarray().ravel()
sorted_by_tfidf = max_value.argsort()
feature_names = np.array(vectorizer.get_feature_names_out())
print("Gesamte Anzahl der Wörter: {}".format(len(vectorizer.vocabulary_)))

Gesamte Anzahl der Wörter: 11592


[Zelle # 10]

1-6: Merkmalen mit höchsten Koeffizienten visualisieren (blau=positiv, rot=negativ). Variable 's_zahl' stellt fest wieviel Merkmalen von beiden Kategorien eingeblendet werden muss. 

7: Gibt den genauen Wert des kleinsten und höchsten Koeffizienten zurück.

In [128]:
# s_zahl = 200
# import matplotlib.pyplot as plt
# import mglearn
# mglearn.tools.visualize_coefficients(
#     grid.best_estimator_.named_steps["logisticregression"].coef_, 
#     feature_names, n_top_features=s_zahl)
# plt.grid()
# #plt.loglog()
# plt.ylim()
# #plt.savefig(gesep+'.jpg', dpi=80)

[Zelle # 11a]

1-7: Extrahieren der Topklassifikationsmerkmalen mit positiven und negativen Werten und ihre Koefizienten.

8-11: Visualisierung der ausgewählten Merkmalen bzw. Koefizienten.

In [129]:
# gio=(grid.best_estimator_.named_steps["logisticregression"].coef_[0])
# n_top=np.argsort(gio)
# z_top=np.sort(gio)
# text_pos=feature_names[n_top[-s_zahl:]]
# text_neg=feature_names[n_top[0:s_zahl]]
# zahl_pos=gio[n_top[-s_zahl:]]
# zahl_neg=gio[n_top[0:s_zahl]]
#print("Positive Merkmale:\n{}".format(text_pos))
#print ("Negative Merkmale:\n{}".format(text_neg))
#print ("Positive coef:\n{}".format(zahl_pos))
#print ("Negative coef:\n{}".format(zahl_neg))

 [Zelle # 11b]
 
 1-7: Berechnung des Schwellenwertes nach der Gleichung (y, x)+(-y, -x) geht die Gleichung auf 0, so ist der Schwellenwert gleich x.
 
 

In [130]:
# kfz=range(s_zahl)
# folgenum=0
# for x in kfz:
#     folgenum+=1
#     vollliste=(zahl_pos[s_zahl-folgenum])+(zahl_neg[s_zahl-folgenum])
#     rundliste=(round(vollliste,3))
#     print(rundliste, '-', x)

[Zelle # 11c]

Schwellenwert für die Variable sw manuel eintragen.

In [131]:
#sw=26

[Zelle # 12]

1-17: Bestimmte Merkmale in die neue txt Datei speichern(1-7) gesamte Information durch die Datenfelder strukturieren (8-12) und  nach dem Löschen der alten Datei (13) in Messdatenordner anlegen (14-17).

In [132]:
import csv
import pandas as pd
df = pd.read_csv('episode_binar_roh.csv', encoding='utf-8')
t_corpus = []
file = 'episode_binar_train.csv'
with open(file, "r", encoding='utf-8') as maerchen:
    maerchen = df.episode
    reader = csv.reader(maerchen, delimiter = ',')
    for row in reader:
        lst = str(row)
        t_corpus.append(lst)
custom_stop_word_list=['test']
import nltk
nltk.download('stopwords')
from nltk.corpus import stopwords
NLTK_stop_words_list=stopwords.words('german')
de = custom_stop_word_list + NLTK_stop_words_list

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\elguj\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


##  Herstellung des Messdatenkorpus 

[Zelle # 13]

1-3: Die Variable 'tupNum', 'repert' und 'ausnahme' gelten für die Auswahl der in dem Messdatenrepositorium angelegte Texte mit dem konkretem Typ und dem Herkunftsrepertoire. Sowohl die Variable 'typNum' ails auch 'repert' kann mit leeren Anführungszeichen dargestellt werden. Für die Variable 'ausnahme' ist entweder ein unwahrscheinlicher Wert (z.B. 'xxyyzz') oder der Wert womit man eine bestimmte Gruppe von Daten aus der Wahl ausschließen kann eine Pflicht.

4: Der vorhandene Messdaten-Korpus löschen (falls vorhanden)

5-7: In dem Messdatenordner Messdaten parsen und einen 'episode_temp_mess.csv' Korpus aggregieren.

8-16: 'episode_temp_mess.csv' von den überflussigen Zeichen bereinigen und ins  Messdatenkorpus - 'episode_binar_mess.csv' umwandeln.

17-21: Datenfelder deklarieren und Datensätzen zählen (s. Counter), anschließend unnotige Temp-Aggregation löschen.

22-29: Messdatenkopus aus den Epsoden bestimmen und alle andere Datenfelder ignorieren

In [151]:
import csv
import pandas as pd
df = pd.read_csv('episode_binar_train.csv', encoding='utf-8')
t_corpus = []
file = 'episode_binar_train.csv'
with open(file, "r", encoding='utf-8') as maerchen:
    maerchen = df.episode
    reader = csv.reader(maerchen, delimiter = ',')
    for row in reader:
        lst = str(row)
        t_corpus.append(lst)
custom_stop_word_list=['test']
import nltk
nltk.download('stopwords')
from nltk.corpus import stopwords
NLTK_stop_words_list=stopwords.words('german')
de = custom_stop_word_list + NLTK_stop_words_list

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\elguj\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


## Vorhersage durch LOGISTICREGRESSION

[Zelle # 14]

1-2: Vorhersage treffen.

3: Der synthetische Datensätzen wird ausgeschloßen. 

4: Jeder positiv bewerteter Datensatz wird extra eingebledet.

In [152]:
mod_pred=grid.predict(t_corpus)
for index in enumerate(mod_pred): 
    if '1' in (index) and index[0]>0:   
        print ('Positiv bewerteter Datensatz:{}'.format(index))

[Zelle # 15]

1-7: Alle probabilitische Vorhersagen abruffen. Durch das Manipulieren der Variable 'pos>=' in der Zeile 6 wird der minimale Score angepasst.

In [153]:
all_pred=grid.predict_proba(t_corpus) 
sort_index=np.flip(all_pred[:,1].argsort())
for num_pos in sort_index:
    pos=all_pred[num_pos][1]
    for i,t_corpus_element in enumerate(t_corpus):
        if i==num_pos  and num_pos>0 :
            print(num_pos,'-', pos,'-', df.quelle[num_pos],'-', df.episode[num_pos])

4543 - 0.00021976424734887836 -  60_Die_zwei_Bruedertxt - nun sprach der koenig an der koeniglichen tafel zu seiner tochter was haben die wilden tiere alle gewollt die zu dir gekommen und in mein schloss ein und ausgegangen sind da antwortete sie ich darfs nicht sagen aber schickt hin und lasst den herrn dieser tiere holen so werdet ihr wohl tun der koenig schickte einen diener ins wirtshaus und liess den fremden mann einladen und der diener kam gerade wie der jaeger mit dem wirt gewettet hatte da sprach er sieht er herr wirt da schickt der koenig einen diener und laesst mich einladen aber ich gehe so noch nicht und zu dem diener sagte er ich lasse den herrn koenig bitten dass er mir koenigliche kleider schickt einen wagen mit sechs pferden und diener die mir aufwarten als der koenig die antwort hoerte sprach er zu seiner tochter was soll ich tun sagte sie lasst ihn holen wie ers verlangt so werdet ihr wohl tun da schickte der koenig koenigliche kleider einen wagen mit sechs pferden un

5501 - 0.00013473251820183258 -  97_Das_Wasser_des_Lebenstxt - der alte koenig war zornig ueber seinen juengsten sohn und glaubte er haette ihm nach dem leben getrachtet also liess er den hof versammeln und das urteil ueber ihn sprechen dass er heimlich sollte erschossen werden als der prinz nun einmal auf die jagd ritt und nichts boeses vermutete musste des koenigs jaeger mitgehen draussen als sie ganz allein im wald waren und der jaeger so traurig aussah sagte der prinz zu ihm lieber jaeger was fehlt dir der jaeger sprach ich kanns nicht sagen und soll es doch da sprach der prinz sage heraus was es ist ich will dirs verzeihen ach sagte der jaeger ich soll euch totschiessen der koenig hat mirs befohlen da erschrak der prinz und sprach lieber jaeger lass mich leben da geb ich dir mein koenigliches kleid gib mir dafuer dein schlechtes der jaeger sagte das will ich gerne tun ich haette doch nicht nach euch schiessen koennen da tauschten sie die kleider und der jaeger ging heim der prinz 

1833 - 0.0001275546603911434 -  20_Horle Horle Wiptxt - es ist ein junger koenig gewesen der reiste in seinem lande umher und liess ein gebot ausgehen in acht tagen solle auf jedem hause ein ordentliches strohdach sein und er liess dabei sagen in acht tagen kaeme er wieder herum wer dann keines haette der solle bestraft werden als die acht tage herum waren ging der koenig umher und fand einen alten mann der kein stroh auf dem dache hatte da fragte der koenig warum er sein gebot nicht erfuellt haette und der alte mann antwortete er koenne kein ordentliches dach haben denn er haette eine tochter die spoenne das stroh vom dache und das moos aus den waenden da fragte der koenig ob er die tochter nicht bekommen koenne der alte mann aber antwortete ja und der koenig nahm die tochter mit nach seinem hause wollte aber erst die probe machen ob sie auch wirklich eine so flinke spinnerin sei am andern tage gab er ihr ein fuder hede und sagte in acht tagen kaeme er wieder dann sollte das fertig ge

3790 - 0.000124998753390789 -  50_Vom_langen_Wintertxt - wie die frau amtmannin das hoert fragt sie sogleich wenn er aus dem himmel sei ob er dann ihren sohn nicht kenne der vor zwei jahren gestorben waere ja sagt er den kenne er wol dem ginge es oben schlecht denn weil er vom lande sei und mit der wirtschaft bescheid wuesste so muesse er oben futter schneiden darueber faengt die frau amtmannin gewaltig an zu lamentiren dass ein amtmannssohn im himmel futter schneiden muesse sie sagt das haette sie nicht gedacht ob sie ihrem sohne denn wol nicht mit etwas geld unter die arme greifen koenne sie haette hier einen beutel mit tausend thalern den sollte sie von ihrem manne ihrem stiefsohne bringen der fortwaehrend in grosser geldverlegenheit sei wenn sie aber wuesste dass ihrem verstorbenen sohne damit geholfen werden koenne so wuerde sie ihm auf der stelle den beutel mit in den himmel schicken denn er sei doch von ihrem eigenen fleisch und blut und ihr stiefsohn koenne warten der kluge man

5022 - 0.00012402616458126207 -  74_Von_Johannes Wassersprung_und_Caspar Wassersprungtxt - indessen kamen die thiere des johannes wassersprung die nach dem kampf sich in die naehe gelagert und auch geschlafen hatten wieder zurueck und fanden ihren herrn todt da sahen sie wie die ameisen denen bei dem kampf ihr huegel zertreten war ihre todten mit dem saft einer nahen eiche bestrichen wovon sie sogleich wieder lebendig wurden der baer ging und holte von dem saft und bestrich den johannes wassersprung davon erholte er sich wieder und in kurzem war er ganz frisch und gesund er gedachte nun an die prinzessin die er sich erkaempft hatte und eilte in die stadt da ward eben die hochzeit mit dem kutscher gefeiert und die leute sagten der habe den siebenkoepfigen drachen getoedtet hund und baer liefen ins schloss wo ihnen die prinzessin braten und wein um den hals band und ihren dienern befahl sie sollten den thieren nachgehen und den mann dem sie angehoerten zur hochzeit laden so kam johannes 

...

1440 - 0.00011362005740844647 -  19_Der_goldene_Becher_die_goldene_Tischdecketxt - es ist ein ding von elfenbein
515 - 0.00011361998467477646 -  12_Doctor_Allwissendtxt - ich bin der doctor allwissend
511 - 0.00011361998467477646 -  12_Doctor_Allwissendtxt - doctor allwissend
5994 - 0.00011361974105779446 -  Das_Maerchen_von_den_sieben_Schwabentxt - i will dohente for di stahn
2712 - 0.00011361965972110412 -  34_Hansens_Trinetxt - 34 hansens trine
542 - 0.0001136196568107482 -  12_Rapunzeltxt - 12 rapunzel
5700 - 0.00011361947215332628 -  B_Literarische_und_mythologische_Anmerkungen_zu_den_Maerchentxt - nr 29
5997 - 0.00011361946158165433 -  Das_Maerchen_von_den_sieben_Schwabentxt - du hoscht sporn und stiefel ahn
4549 - 0.0001136194080450574 -  60_Fleischermeister_Irrlichttxt - 60 fleischermeister irrlicht
776 - 0.00011361933774267645 -  130_Einaeuglein_Zweiaeuglein_und_Dreiaeugleintxt - sang es aus unbedachtsamkeit
7912 - 0.00011361933269172364 -  Gevatterin_Kroetetxt - gevatterin kr

4162 - 0.00011361579708141615 -  56_Der_Liebste_Rolandtxt - der liebste roland
7798 - 0.00011361554193175089 -  Die_schoene_junge_Brauttxt - die freundlich uns entgegenschaut
1002 - 0.00011361542658148493 -  144_Das_Eseleintxt - 144 das eselein
4346 - 0.00011361542658148493 -  58_Das_Eseleintxt - das eselein
7160 - 0.00011361513782657607 -  Der_wandernde_Stabtxt - war wieder von ihnen genommen
6985 - 0.00011361511161502486 -  Der_starke_Gottliebtxt - gottlieb
485 - 0.00011361509464410691 -  119_Die_sieben_Schwabentxt - so zieht denn herzhaft in den streit
5217 - 0.00011361491385421456 -  80_Von_dem_Tode_des_Huehnchenstxt - vorn koennens meine pferdchen nicht vertragen
3090 - 0.00011361473370980068 -  40_Ferenand_getrue_un_Ferenand_ungetruetxt - ferenand ungetrue
600 - 0.00011361473370980068 -  126_Ferenand_getrue_und_Ferenand_ungetruetxt - ferenand ungetrue
4973 - 0.00011361463449853572 -  72_Das_Birnli_will_nit_fallentxt - der schinder will den metzger haenge
8552 - 0.0001136142923358

1870 - 0.00011361048728696041 -  21_Aschenputtel1txt - aschenputtel
4028 - 0.00011361042360264678 -  54_Das_Hausgesindetxt - wo wust du henne  nah
932 - 0.00011361042360264678 -  140_Das_Hausgesindetxt - wo wust du henne nah
3285 - 0.00011361013204250667 -  45_Des_Schneiders_Daumerling_Wanderschafttxt - des schneiders daumerling wanderschaft
5487 - 0.00011361009379213998 -  96_De_drei_Vuegelkenstxt - o kuenig edeles blod
261 - 0.00011361009379213998 -  10_De_drei_Vuegelkenstxt - o kuenig edeles blod
4556 - 0.00011360973671336488 -  61_Das_Buerletxt - 61 das buerle
7090 - 0.000113609667980741 -  Der_wandernde_Stabtxt - ich muede
346 - 0.00011360965762088653 -  108_Hans_mein_Igeltxt - mein maerchen ist aus
4739 - 0.00011360965762088653 -  67_Das_Maerchen_vom_Schlauraffenlandtxt - das maerchen vom schlauraffenland
1116 - 0.00011360965762088653 -  158_Das_Maerchen_vom_Schlauraffenlandtxt - 158 das maerchen vom schlauraffenland
630 - 0.00011360965762088653 -  127_Der_Eisenofentxt - das maer

1785 - 0.00011360440169597637 -  2_Maerchentxt - brock mir wecke und milch ein
5712 - 0.00011360434180772533 -  B_Literarische_und_mythologische_Anmerkungen_zu_den_Maerchentxt - schwert
4408 - 0.00011360420308114315 -  59_Prinz_Schwantxt - mond
1730 - 0.00011360420308114315 -  2_Das_singende_springende_Loeweneckerchentxt - mond
1277 - 0.00011360420308114315 -  175_Der_Mondtxt - 175 der mond
8728 - 0.00011360396175230478 -  Von_einem_Hasen_und_einem_Vogeltxt - zum koenige ausgerufen
6469 - 0.00011360387916730683 -  Der_Schmied_von_Jueterbogktxt - der schmied von jueterbogk
1777 - 0.00011360383416417594 -  2_Maerchen1txt - zweites maerchen
1779 - 0.00011360383416417594 -  2_Maerchentxt - zweites maerchen
5667 - 0.0001136037366963061 -  B_Literarische_und_mythologische_Anmerkungen_zu_den_Maerchentxt - meine bis dahin erschienenen mythologischen sammlungen welches also auch die vorliegende maerchensammlung umfassen soll beizugeben
6271 - 0.00011360372678207317 -  Das_tapfere_Bettelmaennlei

KeyboardInterrupt: 

##  Vorhersage durch die COSINE-SIMILARITY

[Zelle # 16]

1-14: Daten im Messdatenkorpus Vektorisieren, Transformieren und die Metrik für die Vorhersagefunktion definieren.

In [158]:
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.metrics.pairwise import cosine_similarity
vectorizer = TfidfVectorizer
vectorizers = vectorizer(analyzer='word', ngram_range=(1,1), 
                         min_df = 2, stop_words = de)
vokabular =  vectorizers.fit_transform(t_corpus)
metrik = cosine_similarity
def find_similar(vokabular, index, top_n =-1):   
    metriks = metrik(vokabular[index:index+1], vokabular).flatten()
    related_docs_indices = [i for i in metriks.argsort()[::-1] 
                            if i != index]
    return [(index, metriks[index]) for index 
            in related_docs_indices][0:top_n]

[Zelle # 17]

1-3: Gesuchte Episode (Zielepisode) einblenden. Die gesuchte Episode wird wird die 'n_te'-Variable bestimmt. Manuell eingepflegte Zielepisoden sollen deshalb immer in der ersten Reihen der Korpusdatensätzen stehen. Wir empfehlen deshalb, dass diese Daten mit dem Prefix '0_' benannt wird.)

4: Synthetische Datei aus dem Messdatenordner entfernen.

In [159]:
n_te = 0
synt = t_corpus[n_te]
print(df.quelle[n_te],'-', synt)
#entfernen('Messdaten/'+'0_'+gesep+'.txt')

_a - [' als nun der jaeger mit den drei thieren weiter zog kam er in eine stadt die mit schwarzem flor umzogen war er vernahm dass ein drache in der gegend hause der alljaehrlich eine jungfrau verlange in diesem jahre sei die reihe an des koenigs tochter und darum trauere alles der koenig habe sie demjenigen zur frau versprochen der den drachen toedte']


[Zelle # 18]

1-3: Suchen starten und die Ergebnisse einblenden.

In [162]:
for index, score in (find_similar(vokabular, n_te)):
    if (df.index_string[index]==0 or 1):
        print(index,'-', score,'-', df.quelle[index],'-', 
           t_corpus[index], '-',  df.index_binar[index],'-', df.index_binar[index])

4541 - 0.28798370561836417 -  60_Die_zwei_Bruedertxt - ['der jaeger aber war traurig zog in der welt herum und liess seine tiere vor den leuten tanzen es trug sich zu dass er gerade nach verlauf eines jahres wieder in dieselbe stadt kam wo er die koenigstochter vom drachen erloest hatte und die stadt war diesmal ganz mit rotem scharlach ausgehaengt da sprach er zum wirt was will das sagen vorm jahr war die stadt mit schwarzem flor ueberzogen was soll heute der rote scharlach der wirt antwortete vorm jahr sollte unsers koenigs tochter dem drachen ausgeliefert werden aber der marschall hat mit ihm gekaempft und ihn getoetet und da soll morgen ihre vermaehlung gefeiert werden darum war die stadt damals mit schwarzem flor zur trauer und ist heute mit rotem scharlach zur freude ausgehaengt'] - 0 - 0
3016 - 0.26564266112602974 -  4_Der_Jaeger_ueber_alle_Jaegertxt - ['damit war die muehle und die heerde von den riesen erloest und der jaeger ueber alle jaeger setzte seine reise fort er kam in 

4765 - 0.08969477317984154 -  67_Die_zwoelf_Jaegertxt - ['als sie zu der koenigstochter kamen liess diese zwoelf jaegerkleider machen eins wie das andere und die elf jungfrauen mussten die jaegerkleider anziehen und sie selber zog das zwoelfte an darauf nahm sie abschied von ihrem vater und ritt mit ihnen fort und ritt an den hof ihres ehemaligen braeutigams den sie so sehr liebte da fragte sie an ob er jaeger brauchte und ob er sie nicht alle zusammen in seinen dienst nehmen wollte der koenig sah sie an und erkannte sie nicht weil es aber so schoene leute waren sprach er ja er wollte sie gerne nehmen und da waren sie die zwoelf jaeger des koenigs'] - 0 - 0
2566 - 0.08958469166578063 -  32_Der_Reiter_in_Seidentxt - ['der komme mit nach meiner stadt'] - 0 - 0
4698 - 0.08937248390909104 -  65_Allerlei Rauhtxt - ['es war einmal ein koenig der hatte eine frau die war die schoenste auf der welt und hatte haare von purem gold sie hatten auch eine tochter mit einander die war so schoen wie ih

4576 - 0.06751150718053664 -  61_Die_Kaufmannsfrau_als_Obersttxt - ['nun ging in jener stadt der rath auch mitunter in sich und bedachte wo man einen guten trinkt und dabei fiel dann das auge desselben immer gleich auf den rathskeller daneben und mit recht denn alle leute waren darueber einig dass dort der wein viel besser sei als der wirth ja dass in der ganzen stadt kein so guter wein mehr geschenkt werde als im rathskeller wie gesagt darueber waren alle leute in der stadt einig und ein ordentlicher magistrat schwimmt nun einmal nicht ohne noth gegen den strom darum hatten die rathsherren denn nach den sitzungen so ihren zug in den rathskeller und traten auch jetzt eben wieder herein waehrend des gespraeches zischen dem kaufmann und dem wirth'] - 0 - 0
3202 - 0.06742475105564427 -  42_Der_Jaeger_und_die_drei_Bruedertxt - ['in der nacht vor der hinrichtung trat ploetzlich der gruene jaeger in den kerker zu den drei bruedern und hiess sie nur ohne sorgen sein denn es werde noch alles g

6105 - 0.06137490024900496 -  Das_Unentbehrlichstetxt - ['vor zeiten hat einmal ein koenig gelebt der hatte drei gute und schoene toechter die er sehr liebte und von denen er auch herzlich wieder geliebt wurde prinzen hatte er nicht aber es war in seinem reiche herkoemmlich dass die thronfolge auch auf frauen und toechter ueberging und da des koenigs gemahlin nicht mehr am leben war so stand dem koenige frei eine seiner drei prinzessinnen zu seiner nachfolgerin auf dem throne zu bestimmen und es brauchte gerade nicht die aelteste zu sein da aber nun derselbe koenig seine toechter alle drei gleich liebte so fiel ihm die entscheidung schwer und er ging mit sich zu rate diejenige zu waehlen die den meisten scharfsinn offenbare diesen entschluss teilte er seinen drei toechtern mit und bestimmte seinen nahe bevorstehenden geburtstag zur entscheidung'] - 0 - 0
4736 - 0.061316133918188194 -  66_Hurleburlebutztxt - ['ein koenig verirrte sich auf der jagd da trat ein kleines weisses maennchen v

1568 - 0.05606986653895394 -  191_Das_Meerhaeschentxt - ['an dem letzten tag ging er mit schwerem herzen aufs feld und begegnete dem fuchs du weisst alle schlupfwinkel zu finden sprach er ich habe dich leben lassen jetzt rat mir wohin ich mich verstecken soll damit mich die koenigstochter nicht findet ein schweres stueck antwortete der fuchs und machte ein bedenkliches gesicht endlich rief er ich habs heraus er ging mit ihm zu einer quelle tauchte sich hinein und kam als ein marktkraemer und tierhaendler heraus der juengling musste sich auch in das wasser tauchen und ward in ein kleines meerhaeschen verwandelt der kaufmann zog in die stadt und zeigte das artige tierchen es lief viel volk zusammen um es anzusehen zuletzt kam auch die koenigstochter und weil sie grossen gefallen daran hatte kaufte sie es und gab dem kaufmann viel geld dafuer bevor er es ihr hinreichte sagte er zu ihm wenn die koenigstochter ans fenster geht so krieche schnell unter ihren zopf nun kam die zeit wo sie ihn 

...

4944 - 0.0 -  72_Das_Birnli_will_nit_fallentxt - ['da schickt der herr das waesserli naus'] - 0 - 0
4945 - 0.0 -  72_Das_Birnli_will_nit_fallentxt - ['es soll das fuerli loeschen'] - 0 - 0
4946 - 0.0 -  72_Das_Birnli_will_nit_fallentxt - ['das waesserli loescht das fuerli nit'] - 0 - 0
4947 - 0.0 -  72_Das_Birnli_will_nit_fallentxt - ['das fuerli brennt das pruegeli nit'] - 0 - 0
4948 - 0.0 -  72_Das_Birnli_will_nit_fallentxt - ['das pruegeli trifft das huendli nit'] - 0 - 0
4949 - 0.0 -  72_Das_Birnli_will_nit_fallentxt - ['das huendli beisst das jockli nit'] - 0 - 0
4950 - 0.0 -  72_Das_Birnli_will_nit_fallentxt - ['das jockli schuettelts birnli nit'] - 0 - 0
4951 - 0.0 -  72_Das_Birnli_will_nit_fallentxt - ['das birnli will nit fallen'] - 0 - 0
4952 - 0.0 -  72_Das_Birnli_will_nit_fallentxt - ['da schickt der herr das kaelbli naus'] - 0 - 0
4953 - 0.0 -  72_Das_Birnli_will_nit_fallentxt - ['es soll das waesserli laepple trinken'] - 0 - 0
4954 - 0.0 -  72_Das_Birnli_will_nit_fallentx

4824 - 0.0 -  69_Jorinde_und_Joringeltxt - ['mein voeglein mit dem ringlein rot'] - 0 - 0
4825 - 0.0 -  69_Jorinde_und_Joringeltxt - ['singt leide leide leide'] - 0 - 0
4826 - 0.0 -  69_Jorinde_und_Joringeltxt - ['es singt dem taeubelein seinen tod'] - 0 - 0
4827 - 0.0 -  69_Jorinde_und_Joringeltxt - ['singt leide lei  zuckueth zickueth zickueth'] - 0 - 0
4829 - 0.0 -  69_Raethsel Maerchentxt - ['69'] - 0 - 0
4791 - 0.0 -  68_Ein_Windbeutel_legt_das_Kartenspiel_von_einer_guten_Seite_austxt - ['mein herr major wenn ich ohne strafe soll davonkommen so will ich es sagen'] - 0 - 0
4790 - 0.0 -  68_Ein_Windbeutel_legt_das_Kartenspiel_von_einer_guten_Seite_austxt - ['der soldat'] - 0 - 0
4789 - 0.0 -  68_Ein_Windbeutel_legt_das_Kartenspiel_von_einer_guten_Seite_austxt - ['du sagst mir aber doch nichts von dem kreuz bauer welchen du auf die seite gelegt hast sondern sagst er waere nicht ehrlich'] - 0 - 0
4773 - 0.0 -  68_De_Gaudeif_un_sien_Meestertxt - ['68 de gaudeif un sien meester'] - 0 - 

5406 - 0.0 -  9_Die_zwoelf_Bruedertxt - ['9 die zwoelf brueder'] - 0 - 0
5408 - 0.0 -  9_Die_zwoelf_Bruedertxt - ['die mutter aber sass nun den ganzen tag und trauerte so dass der kleinste sohn der immer bei ihr war und den sie nach der bibel benjamin nannte zu ihr sprach liebe mutter warum bist du so traurig liebstes kind antwortete sie ich darf dirs nicht sagen er liess ihr aber keine ruhe bis sie ging und die stube aufschloss und ihm die zwoelf mit hobelspaenen schon gefuellten totenladen zeigte darauf sprach sie mein liebster benjamin diese saerge hat dein vater fuer dich und deine elf brueder machen lassen denn wenn ich ein maedchen zur welt bringe so sollt ihr allesamt getoetet und darin begraben werden und als sie weinte waehrend sie das sprach so troestete sie der sohn und sagte weine nicht liebe mutter wir wollen uns schon helfen und wollen fortgehen sie aber sprach geh mit deinen elf bruedern hinaus in den wald und einer setze sich immer auf den hoechsten baum der zu finden i

5467 - 0.0 -  96_De_drei_Vuegelkenstxt - ['up wietern bescheid'] - 0 - 0
5328 - 0.0 -  88_Das_singende_springende_Loeweneckerchentxt - ['88 das singende springende loeweneckerchen'] - 0 - 0
5321 - 0.0 -  86_Der_Fuchs_und_die_Gaensetxt - ['der fuchs und die gaense'] - 0 - 0
8720 - 0.0 -  Von_einem_Hasen_und_einem_Vogeltxt - ['eine katze ein alter maushund fragte misstrauisch der hase dem traue ich nicht sonderlich das sprichwort sagt die katze laesst das mausen nicht'] - 0 - 0
5209 - 0.0 -  80_Von_dem_Tod_des_Huehnchenstxt - ['von dem tod des huehnchens'] - 0 - 0
5171 - 0.0 -  8_Von_der_Stadt_Sedelfia_und_dem_Vogel_Fabiantxt - ['nach dem vogel fabian'] - 0 - 0
5173 - 0.0 -  8_Von_der_Stadt_Sedelfia_und_dem_Vogel_Fabiantxt - ['o du armer suender rief der faehrmann wie wirds dir ergehen solltest du aber gluecklich davon kommen so erforsche doch woran es liegt dass ich so lange an diesem see schildwache stehen muss und dass niemand mich abloest'] - 0 - 0
5176 - 0.0 -  8_Von_der_Stadt_Sedel

5284 - 0.0 -  83_Hans_im_Gluecktxt - ['83 hans im glueck'] - 0 - 0
5289 - 0.0 -  83_Hans_im_Gluecktxt - ['als er durch das letzte dorf gekommen war stand da ein scherenschleifer mit seinem karren sein rad schnurrte und er sang dazu'] - 0 - 0
5290 - 0.0 -  83_Hans_im_Gluecktxt - ['ich schleife die schere und drehe geschwind'] - 0 - 0
5291 - 0.0 -  83_Hans_im_Gluecktxt - ['und haenge mein maentelchen nach dem wind'] - 0 - 0
5294 - 0.0 -  84_Die_Schwiegermuttertxt - ['84'] - 0 - 0
5295 - 0.0 -  84_Die_Schwiegermuttertxt - ['die schwiegermutter'] - 0 - 0
5297 - 0.0 -  84_Die_Schwiegermuttertxt - ['mit was fuer einer bruehe fragte der koch mit einer braunen sprach die alte koenigin'] - 0 - 0
5299 - 0.0 -  84_Die_Schwiegermuttertxt - ['der koch that so und trug das schweinchen in brauner bruehe auf da waere das kind und sie ass es auf mit grossem appetit'] - 0 - 0
5300 - 0.0 -  84_Die_Schwiegermuttertxt - ['bald darauf dachte die alte das kinderfleisch hat mir so zart geschmeckt du willst da

## Ende 